# Training With an Adversary
### Formalizing adversarial optimization and presenting some attack results

#### First, how can we train a robust classifier?
Neural Networks usually follow the Empirical Risk Minimization (ERM). This works really well!

> $\min \underset{(x,y)\sim \mathcal{D}}{\mathbb{E}} \: \mathcal{L}_{\theta}(x,y)$

But ERM does not discern between robust and non-robust features. Let's force ERM to pick up on robust features. (The proof is straightforward)

> $\min \underset{(x,y)\sim \mathcal{D}}{\mathbb{E}} \: \Big[ \underset{\delta\in\Delta}{\max}\;\; \mathcal{L}_{\theta}\big( x+\delta,y \big) \Big]$

>> The set of allowed perturbations $\Delta = \{ \delta\in \mathbb{R}^{d}\; |\; ||\delta||_{p} \leq \epsilon \}$. $\;\;\delta +x$ is one perturbed input 

Let us consider Projected Gradient Descent as the universal first order adversary. We will use this to train. 
> Repeat $n$ times: $x^{t+1} = \Pi_{x+\Delta}\;\Big[x^{t}+ \epsilon \times sgn \big(\nabla_{x}\; \mathcal{L}(\theta,x,y)\big)\Big]$



### In the case of linear optimization we have
* Convex min, concave max

<img src="other/minmaxsaddle.png">

### In the case of deep neural networks:
* Non-convex min, non-concave max

<img src="other/nnlosssurface.jpeg">

### Integrating Compression into the equation.

A 'neuron' is a linear combination of weights and inputs:

> $x_{out} = \mathbf{W}x_{in} \;\;\;\; \mathbf{W} \in \mathbb{R}^{m\times n},\; m\geq n$

Let us impose

> $\mathbf{W} = \mathbf{U}\mathbf{V}+\mathbf{C}, \;\;\;\; ||\mathbf{U}||_{0}+||\mathbf{V}||_{0}+||\mathbf{C}||_{0} \leq k$


Without going into more detail, this strategy makes it possible to place more rules atop this one


In [4]:
import os, torch 
import pandas as pd
import numpy as np
from src.data_worker import get_data
from src import evaluate
from src.weigh_prune import model_weight_distribution,weigh,get_loss,gen_file_lines
from other.plots import benign_compressed_models, transfer_attacks
from src.attack import ryax_attacker,Carlini_Wagner

import altair as alt
from matplotlib import pyplot as plt

CIFAR10_LABELS = ['airplane','automobile','bird','cat','deer','dog','frog','horse','ship','truck']
CIFAR100_LABELS = sorted(['apples','aquarium','baby','bear','beaver','bed','bee','beetle','bicycle','bottles',
                   'bowls','boy','bridge','bus','butterfly','camel','cans','castle','caterpillar','cattle',
                   'chair','chimpanzee','clock','cloud','cockroach','computer keyboard''couch','crab','crocodile',
                   'cups','dinosaur','dolphin','fish','flatfish','forest','fox','girl','hamster',
                   'house','kangaroo','lamp','lawn-mower','leopard','lion','lizard','lobster','man','maple',
                   'motorcycle','mountain','mouse','mushrooms','oak','oranges','orchids','otter','palm',
                   'pears','pickup','pine','plain','plates','poppies','porcupine','possum','rabbit',
                   'raccoon','ray','road','rocket','roses','sea','seal','shark','shrew','skunk','skyscraper',
                   'snail','snake','spider','squirrel','streetcar','sunflowers','sweet peppers','table',
                   'tank','telephone','television','tiger','tractor','trout','train','truck','tulips',
                      'turtle','wardrobe','whale','willow','wolf','woman','worm'])
CIFAR100_LABELS.sort()
%load_ext autoreload
%autoreload 2

class Mydata:
    @classmethod
    def load_models(cls,d = 'models/cifar10_models/'):
        from src.resnet_model.resnet_dense import ResNet34 as ResNet
        from src.effnet_models.mobilenetv2 import MobileNetV2 as MobNet
        from src.effnet_models.shufflenetv2 import ShuffleNetV2 as ShufNet
        from src.effnet_models.mobilenetv2_cifar100 import MobileNetV2 as MobnetCifar100
        mods = {}
        cls = 100 if '100' in d else 10
        for f in os.listdir(d):
            if ((cls==100) and ('mobilenet' in f)):
                mods[f[:-4]] = MobnetCifar100()
            elif f[-4:]=='.pth':
                mods[f[:-4]] = ResNet(classes=cls) if 'resnet' in f else MobNet(alpha=1.0)
                mods[f[:-4]].load_state_dict(torch.load(d+f), strict = False)
        return mods
                  
    @classmethod
    def load_test_data(cls,batchsz = 1):
        return get_data(test = True,
                     batch_size = batchsz,
                     dataset = 'cifar10',
                     download = False),\
                get_data(test = True,
                     batch_size = batchsz,
                     dataset = 'cifar100',
                     download = False)

def get_CW_atk(m,eps,steps):
    return Carlini_Wagner(model=m,epsilon=eps,steps=steps).get_attack()

def list_dict(d):
    for k,v in sorted(d.items()):
        print(k)

        
c10mods = Mydata.load_models('models/cifar10_models/')
c100mods = Mydata.load_models('models/cifar100_models/')

cifar10,cifar100 = Mydata.load_test_data(1)
cifar10, cifar100 = iter(cifar10), iter(cifar100)

In [5]:
def loss_data_as_df(f):
    return pd.DataFrame(get_loss(gen_file_lines(f)).items(),columns=['iteration','loss'])

def quick_line(df,title =''):
    return alt.Chart(df,width=350,title=title).mark_line().encode(
        x=alt.X('iteration:O',axis=alt.Axis(labels=False,title='',ticks=False)),
        y=alt.Y('loss:Q',axis = alt.Axis(labelFontSize=11,title='',ticks=False)))

def gather_loss_data(d):
    ret = {}
    for item in os.listdir(d):
        ret[item] = loss_data_as_df(d+'/'+item)
    return ret

def showkeys(d):
    for k,v in sorted(d.items()):
        print(k)
    print('\n')
    
ev_resnet = gather_loss_data('logs/train_logs_resnet')
ev_mobnet = gather_loss_data('logs/train_logs_mobnet')

## The loss landscape & finding a saddle point

In [6]:
alt.data_transformers.disable_max_rows()

def put_viz(d):
    full_show = None
    half_show = None
    for k,v in d.items():
        if half_show == None:
            half_show = quick_line(v,title=k)
        else:
            half_show = (half_show | quick_line(v,title=k))
            if full_show == None:
                full_show = half_show
            else:
                full_show = (full_show & half_show)
            half_show = None
    return full_show
       

#d[k] = [v,quick_line(v,title=k)]
#return d
  


put_viz(ev_resnet)
# ev_mobnet = put_viz(ev_mobnet)


# showkeys(ev_resnet)
# showkeys(ev_mobnet) 

alt.VConcatChart(...)

In [4]:
put_viz(ev_mobnet)

alt.VConcatChart(...)

In [5]:
(quick_line(ev_resnet['cifar10_mymethod_8eps']) \
 | quick_line(ev_resnet['cifar10_mymethod_26eps_1pruned_constloss'])\
 | quick_line(ev_resnet['cifar10_mymethod_26eps']))\
&\
(quick_line(ev_mobnet['cifar10mobnet_mymethod_pgd26_1pruned'])\
 | quick_line(ev_mobnet['cifar100mobnet_mymethod_pgd8']) \
 | quick_line(ev_mobnet['cifar10mobnet_mymethod_pgd26']))


alt.VConcatChart(...)

In [6]:
# times = [[90,'100%','cpu'],[82,'50%','cpu'],[46,'100%','gpu'],[44,'50%','gpu']]
# times = pd.DataFrame(times,columns=['Speed(s)','Amt Parameters','Machine'])
# list_dict(c10mods);print('==================');list_dict(c100mods)

# alt.Chart(times,width=200).mark_bar().encode(
#     x='Amt Parameters:N',
#     y='Speed(s):Q',
#     color='Amt Parameters:N',
#     column='Machine:N'
# )

# Transfer Attack
Used to:
- Evaluate empirical robustness under differing **threat models**.
- Assess model compression.

*Is also relevant to distributed ML environments.*

Main Idea:
- White box attack on **threat model A** -> Attack on model B

### Context
<img src=other/edge_architectures.png>

**(a)** On-device computation,   **(b)** Secure two-party computation,   **(c)** Partitioning across edge devices,   **(d)** Model selection and offloading,   **(e)** Partitioning with shared computation


### Testing
<img src=other/transferalgo.png width=750>

In [7]:
transf_resnets8, transf_mobnets8, transf_resnets26, transf_mobnets26 =  transfer_attacks()

def transfer_line(df, dom,rng,legor = 'top-right',offs = 18):
    return alt.Chart(df, width = 500).mark_line(point=True).encode(
        x = alt.X('epsilon:O',
                axis = alt.Axis(title='\u03B5',labelFontSize = 12,titleFontSize=12)),
        y = alt.Y('acc:Q',axis=alt.Axis(title=None, labelFontSize = 12)),
        color = alt.Color('model:N',
                legend=alt.Legend(title=None,labelFontSize=12,orient=legor,offset=offs),
                scale=alt.Scale(
                domain=dom,
                range=rng)))

dom1 = ['Resnet Dense (S)','Resnet 50%','Resnet 10%','Mobilenet Dense','Mobilenet 50%','Mobilenet 10%']
dom2 = ['Mobilenet 10% (S)','Resnet Dense','Resnet 50%','Resnet 10%','Mobilenet Dense','Mobilenet 50%']
rng1 = ['#17202A', '#D4AC0D','#F4D03F','#943126','#CB4335','#EC7063']
rng2 = ['#17202A','#9A7D0A','#D4AC0D','#F4D03F','#943126','#CB4335']



### Models conditioned to $\epsilon \approx 0.03$

In [8]:
transfer_line(transf_resnets8,dom1,rng1)

alt.Chart(...)

In [9]:
transfer_line(transf_mobnets8,dom2,rng2,legor='bottom-right',offs=35)

alt.Chart(...)

In [10]:
transfer_line(transf_resnets26,dom1,rng1) 

alt.Chart(...)

In [11]:
transfer_line(transf_mobnets26,dom2,rng2)

alt.Chart(...)

### Performance Results

In [12]:
def parse_log(l):
    with open(l) as f:
        for line in f:
            yield line.rstrip('\n')

def get_scores(l):
    res = {}
    mob = {}
    model = None
    for item in l:
        if item[:16]=='Running Command:':
            temp = item.split()[2].split('/')[-1][:-4]
            print(temp)
            model = input("Name for this model\n>>>") 
        elif item[:16]=='Benign avg time:':
            if model=='p':
                continue 
            if 'resnet' in temp:
                res[model] = float(item[16:])
            else:
                mob[model] = float(item[16:])
    def iter_dic(d):
        all_data = []
        for k,v in d.items():
            all_data.append([k,v])
        return all_data
    return iter_dic(res),iter_dic(mob)
                   
# res_jetson, mob_jetson = get_scores(parse_log('logs/speed_test_jetson'))
# res_mac,mob_mac = get_scores(parse_log('logs/speed_test_macbook'))

In [14]:
def get_df(l):
    return pd.DataFrame(l,columns=['model','compression','speed'])
jetson_perf  = [
    ['Resnet','Dense', 0.04443714168071747],
    ['Resnet','10%', 0.03818813393115997],
    ['Resnet','50%', 0.03956125612258911],
    ['Mobilenet','Dense',0.06280542964935303],
    ['Mobilenet','10%',0.05782924909591675],
    ['Mobilenet','50%', 0.05907537007331848]]

macbook_perf = [
    ['Resnet','Dense', 0.10534197378158569],
    ['Resnet','10%', 0.0989000810575485229],
    ['Resnet','50%', 0.09975912928581238],
    ['Mobilenet','Dense', 0.021773607492446898],
    ['Mobilenet','10%', 0.015615656995773315],
    ['Mobilenet','50%', 0.017683024406433104]]

nuc_perf =  [
    ['Resnet','Dense',0.063193623447418214 ],
    ['Resnet','10%',0.04928552603721618 ],
    ['Resnet','50%', 0.05321536183357239],
    ['Mobilenet','Dense',0.0104844880104065 ],
    ['Mobilenet','10%',0.008049586534500122 ],
    ['Mobilenet','50%', 0.00933760823726654]]
jetsoncpu_perf = [
    ['Resnet','Dense',3.6193526458740237 ],
    ['Resnet','10%',3.478861927986145 ],
    ['Resnet','50%',3.5228686237335204 ],
    ['Mobilenet','Dense',1.374938735961914 ],
    ['Mobilenet','10%',1.2439255213737487 ],
    ['Mobilenet','50%', 1.3044321393966674]]
cloud_perf = [
    ['Resnet','Dense',0.00784258143901825 ],
    ['Resnet','10%', 0.006942843198776246],
    ['Resnet','50%', 0.00747240052223205],
    ['Mobilenet','Dense', 0.005795733346939087],
    ['Mobilenet','10%',0.00516997196674347 ],
    ['Mobilenet','50%',0.005478161096572876 ]]


def performance_hist(df,title, dom = [0.00,0.12]):
    return alt.Chart(df).mark_bar().encode(
    x = alt.X('compression:O', axis = alt.Axis(title='',labels=False),sort='descending'),
    y = alt.Y('speed:Q', axis = alt.Axis(title=''),scale=alt.Scale(domain=dom)),
    color = alt.Color('compression:O',scale=alt.Scale(scheme='viridis'),
                     legend=alt.Legend(title=None,labelFontSize=12)),
    column = alt.Column('model:N',header=alt.Header(labelFontSize=12,title=title)))

performance_hist( get_df(macbook_perf),title='2013 Macbook Pro CPU' ) | \
performance_hist( get_df(nuc_perf),title='Intel NUC CPU' ) | \
performance_hist( get_df(cloud_perf),title='NVIDIA Tesla V100-PCIE GPU') | \
performance_hist( get_df(jetson_perf),title='Nvidia Jetson Nano GPU' )

alt.HConcatChart(...)

In [13]:
performance_hist( get_df(jetsoncpu_perf),title='Nvidia Jetson Nano CPU', dom=[0.00,4])

alt.Chart(...)

In [30]:
def performance_hist(df,title, dom = [0.00,6.5]):
    return alt.Chart(df).mark_bar().encode(
    x = alt.X('compression:O', axis = alt.Axis(title='',labels=False),sort='descending'),
    y = alt.Y('speed:Q', axis = alt.Axis(title=''),scale=alt.Scale(domain=dom)),
    color = alt.Color('compression:O',scale=alt.Scale(scheme='viridis'),
                     legend=alt.Legend(title=None,labelFontSize=12)),
    column = alt.Column('model:N',header=alt.Header(labelFontSize=12,title=title)))
#NOW PERFORMANCE FOR 100 IMAGES!!
jetson_perf  = [
    ['Resnet','Dense', 1.6809129037],
    ['Resnet','10%', 1.391091237324],
    ['Resnet','50%', 1.5320198412],
    ['Mobilenet','Dense',1.40181346719 ],
    ['Mobilenet','10%', 0.810912308943],
    ['Mobilenet','50%', 0.90121312312]]
macbook_perf = [
    ['Resnet','Dense',6.33913948319175],
    ['Resnet','10%',5.739636473222212],
    ['Resnet','50%',6.006024820154363],
    ['Mobilenet','Dense',1.907988353209062],
    ['Mobilenet','10%',1.23075548258694736],
    ['Mobilenet','50%',1.5575548258694736]]
nuc_perf =  [
    ['Resnet','Dense', 1.3998900],
    ['Resnet','10%', 1.3003421987],
    ['Resnet','50%',1.330719889 ],
    ['Mobilenet','Dense', 0.593415879],
    ['Mobilenet','10%', 0.5075642087],
    ['Mobilenet','50%', 0.542634097]]
jetsoncpu_perf = [
    ['Resnet','Dense',25.39953740 ],
    ['Resnet','10%', 19.99439801],
    ['Resnet','50%', 21.23245287],
    ['Mobilenet','Dense',22.3234234 ],
    ['Mobilenet','10%', 20.19231433],
    ['Mobilenet','50%', 21.33252345]]
cloud_perf = [
    ['Resnet','Dense', 0.02825659738672842],
    ['Resnet','10%', 0.02625659738672842],
    ['Resnet','50%', 0.02725659738672842],
    ['Mobilenet','Dense',0.02861038345865684],
    ['Mobilenet','10%',0.02161038345865684],
    ['Mobilenet','50%',0.02561038345865684 ]]

performance_hist( get_df(macbook_perf),title='2013 Macbook Pro CPU' ) | \
performance_hist( get_df(nuc_perf),title='Intel NUC CPU' ) | \
performance_hist( get_df(cloud_perf),title='NVIDIA Tesla V100-PCIE GPU' ) | \
performance_hist( get_df(jetson_perf),title='Nvidia Jetson Nano GPU' )



alt.HConcatChart(...)

In [31]:
performance_hist( get_df(jetsoncpu_perf),title='Nvidia Jetson Nano CPU', dom=[0.00,25.5])

alt.Chart(...)